# How to make animated heat map combined with choropleth map in folium

## The Basics

In [1]:
import os
import geopandas as gpd
import pandas as pd
import folium
from folium import plugins
from folium.plugins import HeatMap
import branca # color scheme in folium
pd.options.mode.chained_assignment = None

### Part I  Creating choropleth map in a simple way: folium.Choropleth

The coordinate system of raw data is WGS1984, whose unit is in degree and can not be used in area calculation. Therefore, we need to convert it to UTM, calcuate the area, and then change it back for the sake of choropleth map. 

>You could download the data from ArcGIS Online, and export it as shapefile in ArcGIS Pro or Desktop.

In [2]:
fh = gpd.read_file(os.path.join("Data", "CHN_County.shp")).to_crs({'init': 'epsg:3857'})

# Now the area is in square kilometers
fh["Shape__Are"] = fh['geometry'].area/ 10**6 

fh = fh.to_crs(epsg=4326)

Note that this shapefile contains all the counties in China, and I will select those in Shanghai by attribute "ID".

In [3]:
# The list of Shanghai district ID 
shID = ["310101", "310104", "310105", "310106", "310107", "310109", "310110", "310112", "310113", "310114", "310115", "310116", "310117", "310118", "310120", "310151"]

# .isin is used to determine whether this ID is contained in shID (list)
sh_gdf = fh.loc[fh["ID"].isin(shID)]            

sh_gdf

ID                NAME  TOTPOP_CY   Shape__Are  Shape__Len  \
2029  310101    Huangpu District     693708    27.321490    0.198406   
2030  310104      Xuhui District    1130581    74.675655    0.399105   
2031  310105  Changning District     714777    51.178284    0.343986   
2032  310106    Jing'an District    1125112    46.344264    0.356561   
2033  310107      Putuo District    1328734    77.877569    0.514990   
2034  310109    Hongkou District     875180    32.781852    0.245591   
2035  310110     Yangpu District    1356362    84.453330    0.327422   
2036  310112    Minhang District    2596026   510.244414    1.613434   
2037  310113    Baoshan District    2066241   669.523379    2.330605   
2038  310114    Jiading District    1602240   644.602848    1.297954   
2039  310115     Pudong District    5559344  2032.806396    2.579731   
2040  310116    Jinshan District     812885   830.873371    1.899745   
2041  310117  Songjiang District    1779335   836.090435    1.733015   
2042  310118     Qingpu District    1223639   930.360108    2.064315   
2043  310120   Fengxian District    1188458   970.537905    1.271200   
2044  310151  Chongming District     723197  1918.285973    2.101619   

      Shape_Leng  Shape_Area  \
2029    0.198406    0.001886   
2030    0.399105    0.005156   
2031    0.343986    0.003532   
2032    0.356561    0.003197   
2033    0.514990    0.005372   
2034    0.245591    0.002261   
2035    0.327422    0.005823   
2036    1.613434    0.035261   
2037    2.330605    0.046122   
2038    1.297954    0.044419   
2039    2.579731    0.140454   
2040    1.899745    0.057575   
2041    1.733015    0.057824   
2042    2.064315    0.064269   
2043    1.271200    0.067195   
2044    2.101619    0.131784   

                                               geometry  
2029  POLYGON ((121.48400 31.24552, 121.48786 31.244...  
2030  POLYGON ((121.45763 31.21385, 121.45881 31.204...  
2031  POLYGON ((121.33860 31.24426, 121.33864 31.241...  
2032  POLYGON ((121.46060 31.32168, 121.45858 31.307...  
2033  POLYGON ((121.34725 31.30288, 121.35147 31.301...  
2034  POLYGON ((121.48138 31.30554, 121.48580 31.294...  
2035  POLYGON ((121.50313 31.35133, 121.51590 31.345...  
2036  POLYGON ((121.26112 31.25602, 121.26647 31.254...  
2037  MULTIPOLYGON (((121.82468 31.37849, 121.83114 ...  
2038  POLYGON ((121.30155 31.49422, 121.30214 31.493...  
2039  MULTIPOLYGON (((121.97882 31.16125, 121.97082 ...  
2040  MULTIPOLYGON (((121.42528 30.68371, 121.42583 ...  
2041  POLYGON ((121.31185 31.15945, 121.31291 31.158...  
2042  POLYGON ((121.08719 31.28704, 121.08815 31.286...  
2043  MULTIPOLYGON (((121.62940 30.60464, 121.61950 ...  
2044  POLYGON ((121.41028 31.82032, 121.44918 31.793...

Now we could calcualte the population density.

In [4]:
sh_gdf["POP Density"] = round(sh_gdf["TOTPOP_CY"] / sh_gdf["Shape__Are"], 0)  

In addition to geodataframes for attributes (district name & population density), GeoJSON file is also required for its geometry property in choropleth map. 

In [5]:
sh_gjson = sh_gdf.to_json()

We've already got all the necessary data, and it's time for maps!

In [6]:
# Create base map
mp_ch = folium.Map(
    location = [31.2304, 121.4737],
    tiles = "OpenStreetMap",
    zoom_start = 9)

In [7]:
# Create choropleth map
choropleth = folium.Choropleth(
                geo_data = sh_gjson,
                name = "choropleth",
                data = sh_gdf,
                columns=["NAME", "POP Density"],
                key_on = "properties.NAME", 
                fill_color = "YlGn",
                fill_opacity = 0.8,
                line_opacity = 0.2,
                legend_name = "Population density by district in Shanghai")

choropleth.add_to(mp_ch)

folium.LayerControl().add_to(mp_ch)
mp_ch


## A Simple Example

### Part II Creating choropleth map in more complicated way: folium.GeoJSON

>This method provides more flexibility in styling and interactivity, but we need to build a colormap firstly. 

Firstly, create a colormap using branca

In [8]:
colorscale = branca.colormap.linear.YlGn_09.scale(sh_gdf["POP Density"].min(), sh_gdf["POP Density"].max())
colorscale

Now, the color scheme is a gradient, which needs to be a discrete one. Therefore, I'd like to break the gradient into 4 colors and decide the vaules to break at. I've already sort population density in descending order, and assign index to the dataframe.

In [9]:
# Also sort the rows by population density
sh = sh_gdf.sort_values(by=["POP Density"], ascending = False)
sh.reset_index(inplace = True)
sh

index      ID                NAME  TOTPOP_CY   Shape__Are  Shape__Len  \
0    2034  310109    Hongkou District     875180    32.781852    0.245591   
1    2029  310101    Huangpu District     693708    27.321490    0.198406   
2    2032  310106    Jing'an District    1125112    46.344264    0.356561   
3    2033  310107      Putuo District    1328734    77.877569    0.514990   
4    2035  310110     Yangpu District    1356362    84.453330    0.327422   
5    2030  310104      Xuhui District    1130581    74.675655    0.399105   
6    2031  310105  Changning District     714777    51.178284    0.343986   
7    2036  310112    Minhang District    2596026   510.244414    1.613434   
8    2037  310113    Baoshan District    2066241   669.523379    2.330605   
9    2039  310115     Pudong District    5559344  2032.806396    2.579731   
10   2038  310114    Jiading District    1602240   644.602848    1.297954   
11   2041  310117  Songjiang District    1779335   836.090435    1.733015   
12   2042  310118     Qingpu District    1223639   930.360108    2.064315   
13   2043  310120   Fengxian District    1188458   970.537905    1.271200   
14   2040  310116    Jinshan District     812885   830.873371    1.899745   
15   2044  310151  Chongming District     723197  1918.285973    2.101619   

    Shape_Leng  Shape_Area                                           geometry  \
0     0.245591    0.002261  POLYGON ((121.48138 31.30554, 121.48580 31.294...   
1     0.198406    0.001886  POLYGON ((121.48400 31.24552, 121.48786 31.244...   
2     0.356561    0.003197  POLYGON ((121.46060 31.32168, 121.45858 31.307...   
3     0.514990    0.005372  POLYGON ((121.34725 31.30288, 121.35147 31.301...   
4     0.327422    0.005823  POLYGON ((121.50313 31.35133, 121.51590 31.345...   
5     0.399105    0.005156  POLYGON ((121.45763 31.21385, 121.45881 31.204...   
6     0.343986    0.003532  POLYGON ((121.33860 31.24426, 121.33864 31.241...   
7     1.613434    0.035261  POLYGON ((121.26112 31.25602, 121.26647 31.254...   
8     2.330605    0.046122  MULTIPOLYGON (((121.82468 31.37849, 121.83114 ...   
9     2.579731    0.140454  MULTIPOLYGON (((121.97882 31.16125, 121.97082 ...   
10    1.297954    0.044419  POLYGON ((121.30155 31.49422, 121.30214 31.493...   
11    1.733015    0.057824  POLYGON ((121.31185 31.15945, 121.31291 31.158...   
12    2.064315    0.064269  POLYGON ((121.08719 31.28704, 121.08815 31.286...   
13    1.271200    0.067195  MULTIPOLYGON (((121.62940 30.60464, 121.61950 ...   
14    1.899745    0.057575  MULTIPOLYGON (((121.42528 30.68371, 121.42583 ...   
15    2.101619    0.131784  POLYGON ((121.41028 31.82032, 121.44918 31.793...   

    POP Density  
0       26697.0  
1       25391.0  
2       24277.0  
3       17062.0  
4       16060.0  
5       15140.0  
6       13966.0  
7        5088.0  
8        3086.0  
9        2735.0  
10       2486.0  
11       2128.0  
12       1315.0  
13       1225.0  
14        978.0  
15        377.0

Take the 0th, 3th, 7th, 12th and 15th largest vaules to create scheme breaks. 

In [10]:
# creates a list for quantile break 

leg_brks = list(sh[sh.index.isin([0, 3, 7, 12, 15])]["POP Density"])
leg_brks.sort()
print(leg_brks)


[377.0, 1315.0, 5088.0, 17062.0, 26697.0]


In [11]:
colorscale = branca.colormap.linear.YlGn_09.scale(sh_gdf["POP Density"].min(), sh_gdf["POP Density"].max())
colorscale = colorscale.to_step(n = 4, quantiles = leg_brks) # sets quantile breaks

colorscale.caption = "Population density"

colorscale

In [12]:
mp_geo = folium.Map(
    location = [31.2304, 121.4737],
    tiles = "OpenStreetMap",
    zoom_start = 9)

In [13]:
geojsonmap = folium.GeoJson(
                sh_gdf, ## Geopandas dataframe, 
        
                # Apply colorscale based on variables
                style_function = lambda x:{
                    "fillColor": colorscale(x["properties"]["POP Density"]),
                    "fillOpacity":0.7, 
                    "weight": 0.8,
                    "color": "#545453"
                },
        
                # Change styling upon hover
                highlight_function = lambda x:{"fillOpacity":0.4},
    
                # tooltip including district name and population density
                tooltip = folium.features.GeoJsonTooltip(
                    fields = ["NAME", "POP Density"], 
                    aliases = ["District: ", "Population density(km2): "])
)


geojsonmap.add_to(mp_geo)
colorscale.add_to(mp_geo)
folium.LayerControl().add_to(mp_geo)

mp_geo

## A Deeper Dive

### Part III Creating heat map for MOBAI bicycle traces in August, 2016

MOBAI is a bicycle-sharing system in China which is popular in Shanghai. This datasets contains the start & end location and time for each usage.

>Data Source:https://www.kaggle.com/zhuoxibai/mobai-bicycle-traces-shanghai-august

In [14]:
# Drop the column "track" which contains all the GPS location during the usage
df = pd.read_csv(os.path.join("Data", "mobike_shanghai_sample_updated.csv")).drop(columns=["track"]) 

df

orderid  bikeid  userid        start_time  start_location_x  \
0         78387  158357   10080  2016-08-20 06:57           121.348   
1        891333   92776    6605  2016-08-29 19:09           121.508   
2       1106623  152045    8876  2016-08-13 16:17           121.383   
3       1389484  196259   10648  2016-08-23 21:34           121.484   
4        188537   78208   11735  2016-08-16 07:32           121.407   
...         ...     ...     ...               ...               ...   
102356  1479550  214335    1423  2016-08-28 18:03           121.478   
102357  1478273  160487    3067  2016-08-14 20:22           121.320   
102358   367733  179530   12746  2016-08-27 09:54           121.391   
102359    64915  167419     837  2016-08-20 06:04           121.515   
102360   326987   63172    2547  2016-08-09 10:51           121.521   

        start_location_y          end_time  end_location_x  end_location_y  
0                 31.389  2016-08-20 07:04         121.357          31.388  
1                 31.279  2016-08-29 19:31         121.489          31.271  
2                 31.254  2016-08-13 16:36         121.405          31.248  
3                 31.320  2016-08-23 21:43         121.471          31.325  
4                 31.292  2016-08-16 07:41         121.418          31.288  
...                  ...               ...             ...             ...  
102356            31.297  2016-08-28 18:09         121.481          31.304  
102357            31.238  2016-08-14 20:28         121.312          31.235  
102358            31.307  2016-08-27 10:06         121.398          31.306  
102359            31.269  2016-08-20 06:10         121.510          31.272  
102360            31.261  2016-08-09 11:01         121.518          31.274  

[102361 rows x 9 columns]

I will create the map based on start time & location. So, let's split the start time. 

In [15]:
# Create two more columns for day and hour
df.start_time = pd.to_datetime(df.start_time, format= "%Y-%m-%d %H:%M")
df["start_day"] = df.start_time.apply(lambda x: x.day)
df["start_hour"] = df.start_time.apply(lambda x: x.hour)

df.head()

orderid  bikeid  userid          start_time  start_location_x  \
0    78387  158357   10080 2016-08-20 06:57:00           121.348   
1   891333   92776    6605 2016-08-29 19:09:00           121.508   
2  1106623  152045    8876 2016-08-13 16:17:00           121.383   
3  1389484  196259   10648 2016-08-23 21:34:00           121.484   
4   188537   78208   11735 2016-08-16 07:32:00           121.407   

   start_location_y          end_time  end_location_x  end_location_y  \
0            31.389  2016-08-20 07:04         121.357          31.388   
1            31.279  2016-08-29 19:31         121.489          31.271   
2            31.254  2016-08-13 16:36         121.405          31.248   
3            31.320  2016-08-23 21:43         121.471          31.325   
4            31.292  2016-08-16 07:41         121.418          31.288   

   start_day  start_hour  
0         20           6  
1         29          19  
2         13          16  
3         23          21  
4         16           7

In [16]:
# Get rid of unnecessary information
heat_df = df[["start_location_y", "start_location_x", "start_hour"]]

#### (1) Heat Map 
As for heat map, you will need to give it a list of lat, lons, i.e. <b>a list of lists</b>.
>[[lat, lon], [lat, lon], [lat, lon], [lat, lon], [lat, lon]] 

In [17]:
heat_data = [[row["start_location_y"],row["start_location_x"]] for index, row in heat_df.iterrows()]

In [18]:
mp_hmp = folium.Map(
    location = [31.2304, 121.4737],
    tiles = "Stamen Terrain",
    zoom_start = 10)

In [19]:
# Plot it on the map
# I decreased the radius from 15(default) to 8 to make map more clear. 
HeatMap(heat_data, radius = 8, gradient={0.2: 'blue', 0.4: 'lime', 0.6: 'orange', 1: 'red'}, min_opacity = 0.3, max_opacity = 0.5).add_to(mp_hmp)

folium.LayerControl().add_to(mp_hmp)

# Display the map
mp_hmp

#### (2) Heat Map with time series
It adds a time slide to heat map. Also, I believe it will make the map clear since it brings in another variable: time.<br> 
As for heat map with time series, things get more complicated: we need to create <b>a list of lists of lists</b>.
<br><br>In this map, I will organize the list by hour
>List of lists:<br>
 00 = [[lat, lon], [lat, lon], [lat, lon], [lat, lon], [lat, lon]]<br> 
 01 = [[lat, lon], [lat, lon], [lat, lon], [lat, lon], [lat, lon]]<br>
 ...<br><br>
 List of lists of lists:<br>[00, 01, ..., 23]<br>that looks like [[[lat,lon],[lat,lon],[lat,lon]],[[lat,lon],[lat,lon],[lat,lon]],[[lat,lon],[lat,lon],[lat,lon]]]

In [20]:
m_time = folium.Map(
    location = [31.2304, 121.4737],
    tiles = "Stamen Toner",
    zoom_start = 11)

In [21]:
# List comprehension to make out list of lists
heat_time = [[[row["start_location_y"],row["start_location_x"]] for index, row in heat_df[heat_df["start_hour"] == i].iterrows()] for i in range(0,24)]

In [22]:
# Plot it on the map
hm = plugins.HeatMapWithTime(heat_time, gradient={0.2: 'blue', 0.4: 'lime', 0.6: 'orange', 1: 'red'}, min_opacity=0.3, max_opacity=0.8)

hm.add_to(m_time)

# Display the map
m_time

Let's combine the population density choropleth map ahd heat map together.

In [23]:
geojsonmap.add_to(m_time)
colorscale.add_to(m_time)
folium.LayerControl().add_to(m_time)
m_time